In [1]:
!ls  ..

DeepSpeech-2.x	asr  docker.md	ftp.py	proxy.sh  tfe  tts  tutorial


In [2]:
espnet_dir = '../asr/espnet/'
ds2_dir = '../DeepSpeech-2.x/'

In [3]:
!ls $espnet_dir

CONTRIBUTING.md  ci	 egs	 espnet.egg-info  setup.py    tools
LICENSE		 doc	 egs2	 espnet2	  test	      utils
README.md	 docker  espnet  setup.cfg	  test_utils


In [4]:
!ls $ds2_dir

LICENSE       deepspeech  examples	    speechnn	 tmp
README.md     doc	  requirements.txt  tests	 tools
README_cn.md  env.sh	  setup.sh	    third_party  utils


In [182]:
import configargparse
import logging
import os
import random
import sys
import numpy as np

from pprint import pprint
import paddle

In [6]:
#load utt

In [7]:
!ls $espnet_dir/egs/librispeech/asr1/dump/dev_clean/deltafalse/data_unigram5000.json

../asr/espnet//egs/librispeech/asr1/dump/dev_clean/deltafalse/data_unigram5000.json


In [133]:
!ls $espnet_dir/egs/librispeech/asr1/asr1/exp/train_960_pytorch_train_specaug/results/snapshot.ep.27
!cat $espnet_dir/egs/librispeech/asr1/asr1/exp/train_960_pytorch_train_specaug/results/model.json

../asr/espnet//egs/librispeech/asr1/asr1/exp/train_960_pytorch_train_specaug/results/snapshot.ep.27
[
    83,
    5002,
    {
        "accum_grad": 4,
        "adim": 512,
        "aheads": 8,
        "apply_uttmvn": true,
        "backend": "pytorch",
        "badim": 320,
        "batch_bins": 15000000,
        "batch_count": "auto",
        "batch_frames_in": 0,
        "batch_frames_inout": 0,
        "batch_frames_out": 0,
        "batch_size": 0,
        "bdropout_rate": 0.0,
        "beam_size": 4,
        "blayers": 2,
        "bnmask": 2,
        "bprojs": 300,
        "btype": "blstmp",
        "bunits": 300,
        "char_list": [
            "<blank>",
            "<unk>",
            "'",
            "A",
            "ABETH",
            "ABILITY",
            "ABLE",
            "ABLY",
            "ABOUT",
            "AC",
            "ACH",
            "ACIOUS",
            "AD",
            "ADE",
            "AG",
            "AGE",
            "AH",
            "AK"

In [140]:
import json
import logging
import torch
from espnet.asr.asr_utils import add_results_to_json
from espnet.asr.asr_utils import get_model_conf
from espnet.asr.asr_utils import torch_load

from espnet.nets.asr_interface import ASRInterface
from espnet.nets.batch_beam_search import BatchBeamSearch
from espnet.nets.beam_search import BeamSearch
from espnet.nets.lm_interface import dynamic_import_lm
from espnet.nets.scorer_interface import BatchScorerInterface
from espnet.nets.scorers.length_bonus import LengthBonus
from espnet.utils.deterministic_utils import set_deterministic_pytorch
from espnet.utils.io_utils import LoadInputsAndTargets


def make_pad_mask(lengths, xs=None, length_dim=-1):
    if length_dim == 0:
        raise ValueError("length_dim cannot be 0: {}".format(length_dim))

    if not isinstance(lengths, list):
        lengths = lengths.tolist()
    bs = int(len(lengths))
    if xs is None:
        maxlen = int(max(lengths))
    else:
        maxlen = xs.size(length_dim)

    seq_range = torch.arange(0, maxlen, dtype=torch.int64)
    seq_range_expand = seq_range.unsqueeze(0).expand(bs, maxlen)
    seq_length_expand = seq_range_expand.new(lengths).unsqueeze(-1)
    mask = seq_range_expand >= seq_length_expand

    if xs is not None:
        assert xs.size(0) == bs, (xs.size(0), bs)

        if length_dim < 0:
            length_dim = xs.dim() + length_dim
        # ind = (:, None, ..., None, :, , None, ..., None)
        ind = tuple(
            slice(None) if i in (0, length_dim) else None for i in range(xs.dim())
        )
        mask = mask[ind].expand_as(xs).to(xs.device)
    return mask


def make_non_pad_mask(lengths, xs=None, length_dim=-1):
    return ~make_pad_mask(lengths, xs, length_dim)


from espnet.utils.dynamic_import import dynamic_import
def load_trained_model(model_path, training=True):
    """Load the trained model for recognition.

    Args:
        model_path (str): Path to model.***.best

    """
    idim, odim, train_args = get_model_conf(
        model_path, os.path.join(os.path.dirname(model_path), "model.json")
    )

    logging.warning("reading model parameters from " + model_path)

    if hasattr(train_args, "model_module"):
        model_module = train_args.model_module
    else:
        model_module = "espnet.nets.pytorch_backend.e2e_asr:E2E"
    # CTC Loss is not needed, default to builtin to prevent import errors
#     if hasattr(train_args, "ctc_type"):
#         train_args.ctc_type = "builtin"

    model_class = dynamic_import(model_module)

    if "transducer" in model_module:
        model = model_class(idim, odim, train_args, training=training)
        custom_torch_load(model_path, model, training=training)
    else:
        model = model_class(idim, odim, train_args)
        torch_load(model_path, model)

    return model, train_args

# json file

In [72]:
recog_json="../asr/espnet//egs/librispeech/asr1/dump/dev_clean/deltafalse/data_unigram5000.json"
# read json data
with open(recog_json, "rb") as f:
    js = json.load(f)["utts"]

In [73]:
for item in js.items():
    print(item)
    break;

('1272-128104-0000', {'input': [{'feat': '/workspace/zhanghui/asr/espnet/egs/librispeech/asr1/dump/dev_clean/deltafalse/feats.1.ark:17', 'name': 'input1', 'shape': [584, 83]}], 'output': [{'name': 'target1', 'shape': [22, 5002], 'text': 'MISTER QUILTER IS THE APOSTLE OF THE MIDDLE CLASSES AND WE ARE GLAD TO WELCOME HIS GOSPEL', 'token': '▁MISTER ▁QUI L TER ▁IS ▁THE ▁A PO ST LE ▁OF ▁THE ▁MIDDLE ▁CLASSES ▁AND ▁WE ▁ARE ▁GLAD ▁TO ▁WELCOME ▁HIS ▁GOSPEL', 'tokenid': '3008 3630 245 410 2598 4502 482 352 399 252 3204 4502 2974 1165 627 4845 689 2209 4577 4859 2391 2237'}], 'utt2spk': '1272-128104'})


# load model & dump to paddle

In [74]:
ckpt="../asr/espnet//egs/librispeech/asr1/asr1/exp/train_960_pytorch_train_specaug/results/snapshot.ep.27"
model_state_dict = torch.load(ckpt, map_location=lambda storage, loc: storage)["model"]
for key, val in model_state_dict.items():
    print(key, "\t", val.shape, "\t", val.dtype)

encoder.embed.conv.0.weight 	 torch.Size([512, 1, 3, 3]) 	 torch.float32
encoder.embed.conv.0.bias 	 torch.Size([512]) 	 torch.float32
encoder.embed.conv.2.weight 	 torch.Size([512, 512, 3, 3]) 	 torch.float32
encoder.embed.conv.2.bias 	 torch.Size([512]) 	 torch.float32
encoder.embed.out.0.weight 	 torch.Size([512, 10240]) 	 torch.float32
encoder.embed.out.0.bias 	 torch.Size([512]) 	 torch.float32
encoder.encoders.0.self_attn.linear_q.weight 	 torch.Size([512, 512]) 	 torch.float32
encoder.encoders.0.self_attn.linear_q.bias 	 torch.Size([512]) 	 torch.float32
encoder.encoders.0.self_attn.linear_k.weight 	 torch.Size([512, 512]) 	 torch.float32
encoder.encoders.0.self_attn.linear_k.bias 	 torch.Size([512]) 	 torch.float32
encoder.encoders.0.self_attn.linear_v.weight 	 torch.Size([512, 512]) 	 torch.float32
encoder.encoders.0.self_attn.linear_v.bias 	 torch.Size([512]) 	 torch.float32
encoder.encoders.0.self_attn.linear_out.weight 	 torch.Size([512, 512]) 	 torch.float32
encoder.encode

In [75]:
for key, val in model_state_dict.items():
    if 'decoders' in key or 'decoder' in key:
        continue
    print(key, "\t", val.shape, "\t", val.dtype)

encoder.embed.conv.0.weight 	 torch.Size([512, 1, 3, 3]) 	 torch.float32
encoder.embed.conv.0.bias 	 torch.Size([512]) 	 torch.float32
encoder.embed.conv.2.weight 	 torch.Size([512, 512, 3, 3]) 	 torch.float32
encoder.embed.conv.2.bias 	 torch.Size([512]) 	 torch.float32
encoder.embed.out.0.weight 	 torch.Size([512, 10240]) 	 torch.float32
encoder.embed.out.0.bias 	 torch.Size([512]) 	 torch.float32
encoder.encoders.0.self_attn.linear_q.weight 	 torch.Size([512, 512]) 	 torch.float32
encoder.encoders.0.self_attn.linear_q.bias 	 torch.Size([512]) 	 torch.float32
encoder.encoders.0.self_attn.linear_k.weight 	 torch.Size([512, 512]) 	 torch.float32
encoder.encoders.0.self_attn.linear_k.bias 	 torch.Size([512]) 	 torch.float32
encoder.encoders.0.self_attn.linear_v.weight 	 torch.Size([512, 512]) 	 torch.float32
encoder.encoders.0.self_attn.linear_v.bias 	 torch.Size([512]) 	 torch.float32
encoder.encoders.0.self_attn.linear_out.weight 	 torch.Size([512, 512]) 	 torch.float32
encoder.encode

encoder.encoders.8.norm2.bias 	 torch.Size([512]) 	 torch.float32
encoder.encoders.9.self_attn.linear_q.weight 	 torch.Size([512, 512]) 	 torch.float32
encoder.encoders.9.self_attn.linear_q.bias 	 torch.Size([512]) 	 torch.float32
encoder.encoders.9.self_attn.linear_k.weight 	 torch.Size([512, 512]) 	 torch.float32
encoder.encoders.9.self_attn.linear_k.bias 	 torch.Size([512]) 	 torch.float32
encoder.encoders.9.self_attn.linear_v.weight 	 torch.Size([512, 512]) 	 torch.float32
encoder.encoders.9.self_attn.linear_v.bias 	 torch.Size([512]) 	 torch.float32
encoder.encoders.9.self_attn.linear_out.weight 	 torch.Size([512, 512]) 	 torch.float32
encoder.encoders.9.self_attn.linear_out.bias 	 torch.Size([512]) 	 torch.float32
encoder.encoders.9.feed_forward.w_1.weight 	 torch.Size([2048, 512]) 	 torch.float32
encoder.encoders.9.feed_forward.w_1.bias 	 torch.Size([2048]) 	 torch.float32
encoder.encoders.9.feed_forward.w_2.weight 	 torch.Size([512, 2048]) 	 torch.float32
encoder.encoders.9.fee

In [76]:
import paddle
# dump torch model encoder to paddle encoder

def torch_paddle_param(model_state_dict):
    paddle_state_dict = {}
    for n, p in model_state_dict.items():
        print(f'-> {n}    {p.ndim}')
        
        # change norm.mean and norm variance
        name_change=True
        if 'norm.running_mean' in n:
            new_n = n.replace('norm.running_', 'norm._')
        elif 'norm.running_var' in n:
            new_n = n.replace('norm.running_var', 'norm._variance')
        else:
            name_change=False
            new_n = n
        if name_change:
            print(f"{n} -> {new_n}")

        p = p.cpu().detach().numpy()
        
        # weight with is rank 2, transpose it
        if n.endswith('weight') and p.ndim == 2:
            new_p = p.T
            print(f"\t{n}: {p.shape} -> {new_p.shape}")
        else:
            new_p = p
        
        # embedding layer
        if 'decoder.embed.0.weight' in n:
            new_p = p

        if 'global_cmvn.mean' in n:
            print("cmvn:", p, p.dtype)

        paddle_state_dict[new_n] = new_p
    return paddle_state_dict

In [77]:
paddle_model_state_dict = torch_paddle_param(model_state_dict)

-> encoder.embed.conv.0.weight    4
-> encoder.embed.conv.0.bias    1
-> encoder.embed.conv.2.weight    4
-> encoder.embed.conv.2.bias    1
-> encoder.embed.out.0.weight    2
	encoder.embed.out.0.weight: (512, 10240) -> (10240, 512)
-> encoder.embed.out.0.bias    1
-> encoder.encoders.0.self_attn.linear_q.weight    2
	encoder.encoders.0.self_attn.linear_q.weight: (512, 512) -> (512, 512)
-> encoder.encoders.0.self_attn.linear_q.bias    1
-> encoder.encoders.0.self_attn.linear_k.weight    2
	encoder.encoders.0.self_attn.linear_k.weight: (512, 512) -> (512, 512)
-> encoder.encoders.0.self_attn.linear_k.bias    1
-> encoder.encoders.0.self_attn.linear_v.weight    2
	encoder.encoders.0.self_attn.linear_v.weight: (512, 512) -> (512, 512)
-> encoder.encoders.0.self_attn.linear_v.bias    1
-> encoder.encoders.0.self_attn.linear_out.weight    2
	encoder.encoders.0.self_attn.linear_out.weight: (512, 512) -> (512, 512)
-> encoder.encoders.0.self_attn.linear_out.bias    1
-> encoder.encoders.0.fe

In [78]:
for key, val in paddle_model_state_dict.items():
    print(key, "\t", val.shape, "\t", val.dtype)

encoder.embed.conv.0.weight 	 (512, 1, 3, 3) 	 float32
encoder.embed.conv.0.bias 	 (512,) 	 float32
encoder.embed.conv.2.weight 	 (512, 512, 3, 3) 	 float32
encoder.embed.conv.2.bias 	 (512,) 	 float32
encoder.embed.out.0.weight 	 (10240, 512) 	 float32
encoder.embed.out.0.bias 	 (512,) 	 float32
encoder.encoders.0.self_attn.linear_q.weight 	 (512, 512) 	 float32
encoder.encoders.0.self_attn.linear_q.bias 	 (512,) 	 float32
encoder.encoders.0.self_attn.linear_k.weight 	 (512, 512) 	 float32
encoder.encoders.0.self_attn.linear_k.bias 	 (512,) 	 float32
encoder.encoders.0.self_attn.linear_v.weight 	 (512, 512) 	 float32
encoder.encoders.0.self_attn.linear_v.bias 	 (512,) 	 float32
encoder.encoders.0.self_attn.linear_out.weight 	 (512, 512) 	 float32
encoder.encoders.0.self_attn.linear_out.bias 	 (512,) 	 float32
encoder.encoders.0.feed_forward.w_1.weight 	 (512, 2048) 	 float32
encoder.encoders.0.feed_forward.w_1.bias 	 (2048,) 	 float32
encoder.encoders.0.feed_forward.w_2.weight 	 (2048

In [79]:
for key, val in model_state_dict.items():
    if 'decoder.embed.0.weight' in key:
        val = val
    elif key.endswith('weight') and val.ndim == 2:
        val = val.T  
    print(np.allclose(val, paddle_model_state_dict[key]))

True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True
True


# load input and output

In [80]:
load_inputs_and_targets = LoadInputsAndTargets(
        mode="asr",
        load_input=True,
        load_output=True,
        sort_in_input_length=False,
        preprocess_conf=None,
        preprocess_args={"train": False},
    )

In [81]:
with torch.no_grad():
        idx = 0
        name = list(js.keys())[idx]
        logging.info("(%d/%d) decoding " + name, idx, len(js.keys()))
        batch = [(name, js[name])]
        print(batch, '\n')
        bdata = load_inputs_and_targets(batch)
        print(len(bdata))
        feat = bdata[0][0]
        label = bdata[1][0]
        print(feat)
        print(label)

[('1272-128104-0000', {'input': [{'feat': '/workspace/zhanghui/asr/espnet/egs/librispeech/asr1/dump/dev_clean/deltafalse/feats.1.ark:17', 'name': 'input1', 'shape': [584, 83]}], 'output': [{'name': 'target1', 'shape': [22, 5002], 'text': 'MISTER QUILTER IS THE APOSTLE OF THE MIDDLE CLASSES AND WE ARE GLAD TO WELCOME HIS GOSPEL', 'token': '▁MISTER ▁QUI L TER ▁IS ▁THE ▁A PO ST LE ▁OF ▁THE ▁MIDDLE ▁CLASSES ▁AND ▁WE ▁ARE ▁GLAD ▁TO ▁WELCOME ▁HIS ▁GOSPEL', 'tokenid': '3008 3630 245 410 2598 4502 482 352 399 252 3204 4502 2974 1165 627 4845 689 2209 4577 4859 2391 2237'}], 'utt2spk': '1272-128104'})] 

2
[[-0.74641937 -0.58889526 -0.79081845 ...  1.2798967   0.22447938
  -0.11255249]
 [-0.74641937 -0.574557   -0.9586555  ...  1.3187659   0.24862868
   0.06486106]
 [-0.51503205 -0.41683638 -0.6949115  ...  1.3654089   0.28082776
   0.04357147]
 ...
 [-0.65000796 -0.54588056 -0.9586555  ...  0.7260699  -0.24240735
  -0.19061443]
 [-0.74641937 -0.6175717  -0.8387718  ...  0.7131443  -0.2343576
 

In [82]:
!ls $espnet_dir/egs/librispeech/asr1/asr1/exp/train_960_pytorch_train_specaug/results

acc.png		model.loss.best  snapshot.ep.16  snapshot.ep.23  snapshot.ep.6
att_ws		snapshot.ep.1	 snapshot.ep.17  snapshot.ep.24  snapshot.ep.7
ctc_prob	snapshot.ep.10	 snapshot.ep.18  snapshot.ep.25  snapshot.ep.8
log		snapshot.ep.11	 snapshot.ep.19  snapshot.ep.26  snapshot.ep.9
loss.png	snapshot.ep.12	 snapshot.ep.2	 snapshot.ep.27
model.acc.best	snapshot.ep.13	 snapshot.ep.20  snapshot.ep.3
model.json	snapshot.ep.14	 snapshot.ep.21  snapshot.ep.4
model.json.bak	snapshot.ep.15	 snapshot.ep.22  snapshot.ep.5


In [83]:
model, train_args = load_trained_model(ckpt)
model.eval()
print(model)
print(train_args)

E2E(
  (encoder): Encoder(
    (embed): Conv2dSubsampling(
      (conv): Sequential(
        (0): Conv2d(1, 512, kernel_size=(3, 3), stride=(2, 2))
        (1): ReLU()
        (2): Conv2d(512, 512, kernel_size=(3, 3), stride=(2, 2))
        (3): ReLU()
      )
      (out): Sequential(
        (0): Linear(in_features=10240, out_features=512, bias=True)
        (1): PositionalEncoding(
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
    )
    (encoders): MultiSequential(
      (0): EncoderLayer(
        (self_attn): MultiHeadedAttention(
          (linear_q): Linear(in_features=512, out_features=512, bias=True)
          (linear_k): Linear(in_features=512, out_features=512, bias=True)
          (linear_v): Linear(in_features=512, out_features=512, bias=True)
          (linear_out): Linear(in_features=512, out_features=512, bias=True)
          (dropout): Dropout(p=0.0, inplace=False)
        )
        (feed_forward): PositionwiseFeedForward(
          (w_1): Linear(i

In [84]:
device='cpu'
with torch.no_grad():
    enc = model.encode(torch.as_tensor(feat).to(device=device))
    print(enc.numpy())

[[ 0.0084809  -0.03854299  0.05893369 ...  0.02430487 -0.04398455
  -0.05841548]
 [ 0.00554978 -0.03724072  0.05680261 ...  0.02338517 -0.03312957
  -0.05391716]
 [ 0.00168099 -0.04298185  0.06165742 ...  0.02442379 -0.0287394
  -0.05569264]
 ...
 [ 0.23188232  0.0513467  -0.02806944 ...  0.02038751  0.00450835
  -0.207303  ]
 [ 0.3011615   0.0425128  -0.00147884 ... -0.03319022 -0.01043977
  -0.20581883]
 [ 0.32673094  0.0756444  -0.04818322 ... -0.04932987  0.02738191
  -0.23118067]]


In [85]:
# def recog_v2(args):
#     """Decode with custom models that implements ScorerInterface.

#     Notes:
#         The previous backend espnet.asr.pytorch_backend.asr.recog
#         only supports E2E and RNNLM

#     Args:
#         args (namespace): The program arguments.
#         See py:func:`espnet.bin.asr_recog.get_parser` for details

#     """
#     set_deterministic_pytorch(args)
#     model, train_args = load_trained_model(args.model)

#     model.eval()

#     if args.ngpu == 1:
#         device = "cuda"
#     else:
#         device = "cpu"
#     dtype = getattr(torch, args.dtype)

#     model.to(device=device, dtype=dtype).eval()
#     with torch.no_grad():
#         for idx, name in enumerate(js.keys(), 1):
#             logging.info("(%d/%d) decoding " + name, idx, len(js.keys()))
#             batch = [(name, js[name])]
#             feat = load_inputs_and_targets(batch)[0][0]
#             enc = model.encode(torch.as_tensor(feat).to(device=device, dtype=dtype))
#             nbest_hyps = beam_search(
#                 x=enc, maxlenratio=args.maxlenratio, minlenratio=args.minlenratio
#             )
#             nbest_hyps = [
#                 h.asdict() for h in nbest_hyps[: min(len(nbest_hyps), args.nbest)]
#             ]
#             new_js[name] = add_results_to_json(
#                 js[name], nbest_hyps, train_args.char_list
#             )


# def torch_load(path, model):
#     """Load torch model states.

#     Args:
#         path (str): Model path or snapshot file path to be loaded.
#         model (torch.nn.Module): Torch model.

#     """
#     if "snapshot" in os.path.basename(path):
#         model_state_dict = torch.load(path, map_location=lambda storage, loc: storage)[
#             "model"
#         ]
#     else:
#         model_state_dict = torch.load(path, map_location=lambda storage, loc: storage)

#     if hasattr(model, "module"):
#         model.module.load_state_dict(model_state_dict)
#     else:
#         model.load_state_dict(model_state_dict)

#     del model_state_dict

In [86]:
x = np.expand_dims(feat, 0)
ilen = np.array(feat.shape[1]).reshape(1)
y = np.expand_dims(label, 0)
print(x.shape)
print(ilen.shape)
print(y.shape)
loss = model(
    torch.as_tensor(x).to(device=device), 
    torch.as_tensor(ilen).to(device),
    torch.as_tensor(y).to(device))
print(loss)
print(loss.grad)

(1, 584, 83)
(1,)
(1, 22)
tensor(115.3222, grad_fn=<AddBackward0>)
None


<ipython-input-86-81ae1e6efdc8>:12: UserWarning: The .grad attribute of a Tensor that is not a leaf Tensor is being accessed. Its .grad attribute won't be populated during autograd.backward(). If you indeed want the gradient for a non-leaf Tensor, use .retain_grad() on the non-leaf Tensor. If you access the non-leaf Tensor by mistake, make sure you access the leaf Tensor instead. See github.com/pytorch/pytorch/pull/30531 for more informations.
  print(loss.grad)


In [87]:
# encoder + ctc  grad

In [88]:
!ls ../asr/espnet//egs/librispeech/asr1/asr1/exp/train_960_pytorch_train_specaug/results/

acc.png		model.loss.best  snapshot.ep.16  snapshot.ep.23  snapshot.ep.6
att_ws		snapshot.ep.1	 snapshot.ep.17  snapshot.ep.24  snapshot.ep.7
ctc_prob	snapshot.ep.10	 snapshot.ep.18  snapshot.ep.25  snapshot.ep.8
log		snapshot.ep.11	 snapshot.ep.19  snapshot.ep.26  snapshot.ep.9
loss.png	snapshot.ep.12	 snapshot.ep.2	 snapshot.ep.27
model.acc.best	snapshot.ep.13	 snapshot.ep.20  snapshot.ep.3
model.json	snapshot.ep.14	 snapshot.ep.21  snapshot.ep.4
model.json.bak	snapshot.ep.15	 snapshot.ep.22  snapshot.ep.5


In [90]:
with torch.no_grad():
        idx = 1
        name = list(js.keys())[idx]
        logging.info("(%d/%d) decoding " + name, idx, len(js.keys()))
        batch = [(name, js[name])]
        print(batch, '\n')
        bdata = load_inputs_and_targets(batch)
        print(len(bdata))
        feat2 = bdata[0][0]
        label2 = bdata[1][0]
        print(feat2)
        print(label2)

[('1272-128104-0001', {'input': [{'feat': '/workspace/zhanghui/asr/espnet/egs/librispeech/asr1/dump/dev_clean/deltafalse/feats.1.ark:49191', 'name': 'input1', 'shape': [480, 83]}], 'output': [{'name': 'target1', 'shape': [14, 5002], 'text': "NOR IS MISTER QUILTER'S MANNER LESS INTERESTING THAN HIS MATTER", 'token': "▁NOR ▁IS ▁MISTER ▁QUI L TER ' S ▁MANNER ▁LESS ▁INTERESTING ▁THAN ▁HIS ▁MATTER", 'tokenid': '3152 2598 3008 3630 245 410 2 389 2893 2770 2572 4499 2391 2926'}], 'utt2spk': '1272-128104'})] 

2
[[-0.5260203  -0.440242   -0.8399645  ...  1.4257575  -0.46800017
  -0.44417572]
 [-0.40732563 -0.37577838 -0.72303843 ...  1.4127053  -0.5211444
  -0.33839935]
 [-0.57349813 -0.40801018 -0.69965315 ...  1.4518621  -0.5683837
   0.13844776]
 ...
 [-0.8108874  -0.6497487  -0.9568907  ...  1.2756567  -1.032064
  -0.38541245]
 [-0.71593165 -0.5047056  -0.7464236  ...  1.3735485  -1.0094705
   0.1451639 ]
 [-0.47854233 -0.440242   -0.9335055  ...  1.3996531  -0.96428335
  -0.38541245]]
[31

# 载入模型，准备输入

In [91]:
model_raw, train_args = load_trained_model(ckpt)


In [92]:
x = np.expand_dims(feat, 0)
ilen = np.array(feat.shape[0]).reshape(1)
y = np.expand_dims(label, 0)
olen = np.array(len(label)).reshape(1)
print(x.shape)
print(ilen)
print(ilen.shape)
print(y.shape)
print(y)
print(olen)

device='cpu'
model.to(device)
model.zero_grad()
print(model.adim)

xs_pad = torch.as_tensor(x).to(device=device)
ilens = torch.as_tensor(ilen).to(device)
ys_pad = torch.as_tensor(y).to(device)

(1, 584, 83)
[584]
(1,)
(1, 22)
[[3008 3630  245  410 2598 4502  482  352  399  252 3204 4502 2974 1165
   627 4845  689 2209 4577 4859 2391 2237]]
[22]
512


# 获取foward input & output, grad

In [93]:
model = model_raw
model.eval()

def numpy_from_tensor(xx):
    if isinstance(xx, (list, tuple)):
        return [numpy_from_tensor(x) for x in xx]
    if isinstance(xx, dict):
        return {key: numpy_from_tensor(val) for key, val in xx}
    if xx is None:
        return None
    if isinstance(xx, torch.Tensor): 
        return xx.detach().numpy()
    return xx


forward_dict={}
backward_dict={}
def forward_hook(m, ins, outs):
    for n, mod in model.named_modules():
        if m is mod:
            forward_dict[n] = {
                'inputs': numpy_from_tensor(ins),
                'outputs':  numpy_from_tensor(outs),
            }
    
def backward_hook(m, grad_ins, grad_outs):
     if grad_outs is None or grad_outs[0] is None:
            return
     for n, mod in model.named_modules():
        if m is mod:
            backward_dict[n] = {
                'grad_outs': numpy_from_tensor(grad_outs),
                'grad_ins': numpy_from_tensor(grad_ins),
            }

            
for n, m in model.named_modules():
    if isinstance(m, torch.nn.Module):
        try:
            m.register_forward_hook(forward_hook)
            m.register_backward_hook(backward_hook)
        except Exception as e:
            print(n)
        

In [94]:
print(forward_dict)

{}


In [128]:
def to_device(m, x):
    """Send tensor into the device of the module.

    Args:
        m (torch.nn.Module): Torch module.
        x (Tensor): Torch tensor.

    Returns:
        Tensor: Torch tensor located in the same place as torch module.

    """
    if isinstance(m, torch.nn.Module):
        device = next(m.parameters()).device
    elif isinstance(m, torch.Tensor):
        device = m.device
    else:
        raise TypeError(
            "Expected torch.nn.Module or torch.tensor, " f"bot got: {type(m)}"
        )
    return x.to(device)


class CTC(torch.nn.Module):

    def __init__(self, odim, eprojs, dropout_rate, ctc_type="warpctc", reduce=True):
        super().__init__()
        self.dropout_rate = 0
        self.loss = None
        self.ctc_lo = torch.nn.Linear(eprojs, odim)
        self.probs = None  # for visualization

        # In case of Pytorch >= 1.7.0, CTC will be always builtin
        self.ctc_type = ctc_type
          
        if ctc_type != self.ctc_type:
            logging.warning(f"CTC was set to {self.ctc_type} due to PyTorch version.")

        if self.ctc_type == "warpctc":
            import warpctc_pytorch as warp_ctc
            self.ctc_loss = warp_ctc.CTCLoss(size_average=True, reduce=reduce)
        else:
            raise ValueError(
                'ctc_type must be "builtin" or "warpctc": {}'.format(self.ctc_type)
            )

        self.ignore_id = -1
        self.reduce = reduce

    def loss_fn(self, th_pred, th_target, th_ilen, th_olen):
        if self.ctc_type == "warpctc":
            return self.ctc_loss(th_pred, th_target, th_ilen, th_olen)
        else:
            raise NotImplementedError

    def forward(self, hs_pad, hlens, ys_pad):
        ys = [y[y != self.ignore_id] for y in ys_pad]  # parse padded ys

        ys_hat = self.ctc_lo(hs_pad)
        if self.ctc_type != "gtnctc":
            ys_hat = ys_hat.transpose(0, 1)

        self.loss = None
        hlens = torch.from_numpy(np.fromiter(hlens, dtype=np.int32))
        olens = torch.from_numpy(
            np.fromiter((x.size(0) for x in ys), dtype=np.int32)
        )
        # zero padding for ys
        ys_true = torch.cat(ys).cpu().int()  # batch x olen
        # get ctc loss
        # expected shape of seqLength x batchSize x alphabet_size
        dtype = ys_hat.dtype
        if self.ctc_type == "warpctc" or dtype == torch.float16:
            # warpctc only supports float32
            # torch.ctc does not support float16 (#1751)
            ys_hat = ys_hat.to(dtype=torch.float32)

        self.loss = to_device(
            hs_pad, self.loss_fn(ys_hat, ys_true, hlens, olens)
        ).to(dtype=dtype)

        if self.reduce:
            # NOTE: sum() is needed to keep consistency
            # since warpctc return as tensor w/ shape (1,)
            # but builtin return as tensor w/o shape (scalar).
            self.loss = self.loss.sum()
            logging.info("ctc loss:" + str(float(self.loss)))

        return self.loss

In [122]:
torch.__version__

'1.6.0'

In [170]:
model.zero_grad()
for key, val in model.named_parameters():
    if 'ctc' not in key:
        continue
    if 'weight' in key:
        print(key, val.grad.t())
    else:
        print(key, val.grad)

ctc.ctc_lo.weight tensor([[0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        ...,
        [0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.]])
ctc.ctc_lo.bias tensor([0., 0., 0.,  ..., 0., 0., 0.])


In [171]:
model.eval()
model.ctc.eval()
model.ctc.dropout_rate = 0.0

# encoder
xs_pad = xs_pad[:, : max(ilens)]
src_mask = make_non_pad_mask(ilens.tolist()).to(xs_pad.device).unsqueeze(-2)
hs_pad, hs_mask = model.encoder(xs_pad, src_mask)
print(hs_pad.sum().detach().numpy())

# ctc loss
batch_size = xs_pad.size(0)
hs_len = hs_mask.view(batch_size, -1).sum(1)
loss = model.ctc(hs_pad.view(batch_size, -1, model.adim), hs_len, ys_pad)
print('loss', loss.detach().numpy())
print(model.ctc)
loss.retain_grad()
loss.backward()
print(loss.grad)

# # warpctc w/o dropout
# ctc = CTC(5002,512, 0)
# ctc.ctc_lo.weight = model.ctc.ctc_lo.weight
# ctc.ctc_lo.bias = model.ctc.ctc_lo.bias
# loss_b = ctc(hs_pad.view(batch_size, -1, model.adim), hs_len, ys_pad)
# print(loss_b)

122.53613
loss 5.9801354
CTC(
  (ctc_lo): Linear(in_features=512, out_features=5002, bias=True)
  (ctc_loss): CTCLoss()
)
tensor(1.)


In [137]:
# outproject linear
lo = model.ctc.ctc_lo(hs_pad.view(batch_size, -1, model.adim))
print(lo.detach().numpy().sum())
print(lo.detach().numpy())
paddle.save({'lo': lo.detach().numpy(), 
             'hs_len':hs_len.detach().numpy(),
            'ys_pad':ys_pad.detach().numpy(),
            'ys_len':ys_pad.size(1)}, 'ctc_lo')
print(ys_pad.size(1))
print(hs_len)
print(ys_pad)

-8020950.0
[[[ 22.989422   -14.030043     6.0457883  ...   3.0186079   -0.23548293
   -14.020504  ]
  [ 23.250462   -13.562406     6.260898   ...   3.5122383    0.09232712
   -13.554235  ]
  [ 23.280766   -13.543007     6.225544   ...   3.5360448    0.14748597
   -13.537972  ]
  ...
  [ 13.485205   -23.31453     -0.3501923  ...  -7.0977297   -8.506543
   -23.212677  ]
  [ 14.065702   -22.272661     0.30908418 ...  -5.896199    -7.6193686
   -22.165726  ]
  [ 13.672498   -22.783966     0.1425507  ...  -6.2963276   -8.160887
   -22.68066   ]]]
22
tensor([145])
tensor([[3008, 3630,  245,  410, 2598, 4502,  482,  352,  399,  252, 3204, 4502,
         2974, 1165,  627, 4845,  689, 2209, 4577, 4859, 2391, 2237]])


In [141]:
for key, val in model.named_parameters():
    if val.grad is None:
        continue
    print(key, "\t",  val.grad.detach().numpy())

encoder.embed.conv.0.weight 	 [[[[   0.         0.         0.     ]
   [   0.         0.         0.     ]
   [   0.         0.         0.     ]]]


 [[[-335.24658 -366.7305  -340.28928]
   [-375.515   -389.5845  -380.37064]
   [-356.9231  -354.5135  -417.6492 ]]]


 [[[   0.         0.         0.     ]
   [   0.         0.         0.     ]
   [   0.         0.         0.     ]]]


 ...


 [[[   0.         0.         0.     ]
   [   0.         0.         0.     ]
   [   0.         0.         0.     ]]]


 [[[   0.         0.         0.     ]
   [   0.         0.         0.     ]
   [   0.         0.         0.     ]]]


 [[[   0.         0.         0.     ]
   [   0.         0.         0.     ]
   [   0.         0.         0.     ]]]]
encoder.embed.conv.0.bias 	 [   0.        -252.51706      0.           0.           0.
    0.           0.           0.           0.           0.
    0.           0.        -147.28784      0.           0.
  117.18473      0.           0.           0.      

encoder.encoders.4.norm1.bias 	 [ 5.66896248e+00 -5.84763336e+00 -2.61223507e+00 -1.52511406e+01
 -2.80434585e+00  1.62391682e+01  4.50009394e+00  2.07968855e+00
 -1.79179020e+01  1.37437897e+01  7.92345715e+00  1.71809807e+01
  8.59227180e+00 -3.27081513e+00  3.28606081e+00  1.76282959e+01
  5.21873140e+00  7.75166750e-01  1.07146349e+01  1.61132069e+01
 -1.48009348e+01 -1.57639961e+01 -1.13102064e+01  1.41489964e+01
  4.46127367e+00  1.11286039e+01 -6.45562935e+00 -1.37329311e+01
  3.00916052e+00 -4.36561775e+00  8.37098503e+00 -3.31968570e+00
 -2.60748315e+00  1.92783127e+01 -8.14757586e-01 -4.41519827e-01
 -1.41470881e+01 -1.41165829e+01 -5.82860994e+00  1.03465986e+01
 -3.12779846e+01  1.86029758e+01  9.64246559e+00  5.05928218e-01
 -1.23436394e+01 -3.11348581e+00  4.84917021e+00 -1.38473570e+00
 -1.21502123e+01 -9.00640249e-01  2.16777849e+00 -1.49400890e+00
 -2.40898585e+00  8.86334610e+00  1.31477809e+00  9.96801186e+00
 -1.65438690e+01 -3.62290311e+00 -1.14541874e+01  1.260569

encoder.encoders.9.norm2.bias 	 [-5.7525091e+00 -1.6512340e+00  5.8853946e+00  2.0378830e+00
 -2.5953531e-01 -1.4698613e+00  8.5416870e+00  2.9250641e+00
  5.3714114e-01  3.2625108e+00 -4.1959634e+00  5.3563380e+00
  2.9226954e+00 -9.6510750e-01  5.2836695e+00 -1.0151606e+00
  1.4500626e+00  3.5970393e-01  1.3999267e+00  6.6158712e-02
 -4.6101627e+00 -3.6827698e+00 -2.6958101e+00  2.3686888e+00
 -8.7943659e+00 -9.1280651e-01 -9.1016710e-01 -1.1902022e+00
 -6.0231676e+00  4.8172460e+00  1.5913813e-01  2.0039554e+00
  2.8951383e+00 -9.9214926e+00 -1.1689790e+00 -8.3481234e-01
 -6.4273005e+00 -2.6799879e+00 -4.9759150e+00 -3.8854496e+00
 -4.8155761e+00  3.2136462e+00 -2.6005671e+00 -8.7414372e-01
 -2.1125128e+00  5.1343098e+00 -1.0350186e+01 -4.5495553e+00
 -1.0921682e+00  3.0346916e+00 -1.6189908e+00  3.5228961e+00
  8.6831886e-01 -9.2598066e+00  5.6160450e+00 -7.0793071e+00
  3.7679982e+00  1.1589026e+00  2.8514073e+00 -2.0372882e+00
 -3.8768306e+00  7.0595984e+00  2.8590301e-01 -2.3442

In [179]:
pprint(list(forward_dict.items()))

[('encoder.embed.conv.0',
  {'inputs': [array([[[[-0.74641937, -0.58889526, -0.79081845, ...,  1.2798967 ,
           0.22447938, -0.11255249],
         [-0.74641937, -0.574557  , -0.9586555 , ...,  1.3187659 ,
           0.24862868,  0.06486106],
         [-0.51503205, -0.41683638, -0.6949115 , ...,  1.3654089 ,
           0.28082776,  0.04357147],
         ...,
         [-0.65000796, -0.54588056, -0.9586555 , ...,  0.7260699 ,
          -0.24240735, -0.19061443],
         [-0.74641937, -0.6175717 , -0.8387718 , ...,  0.7131443 ,
          -0.2343576 ,  0.11453688],
         [-0.47646755, -0.37382168, -0.79081845, ...,  1.0933245 ,
          -0.2343576 ,  0.44807434]]]], dtype=float32)],
   'outputs': array([[[[-2.3296108e+00, -2.3804862e+00, -2.2985189e+00, ...,
          -2.2790453e+00, -1.7673831e+00, -2.1839311e+00],
         [-2.4855013e+00, -2.5069976e+00, -2.5415361e+00, ...,
          -2.0678055e+00, -1.9863954e+00, -2.2065032e+00],
         [-2.1821668e+00, -2.6111586e+00, -2

 ('encoder.encoders.1.norm2',
  {'inputs': [array([[[ -3.5859313 ,  36.152092  , -18.13733   , ...,  -9.173916  ,
          13.070941  , -10.725042  ],
        [  0.14832401,  23.283823  , -24.295023  , ...,  -2.9770672 ,
           9.696861  ,  14.843302  ],
        [  1.9228532 ,  12.94478   , -16.441635  , ...,   5.411833  ,
          22.807425  ,   2.5184999 ],
        ...,
        [-23.59988   ,  22.983461  , -19.18822   , ..., -25.252907  ,
           9.484108  ,  -5.978131  ],
        [-32.06284   ,  23.38433   , -29.370281  , ...,   2.7941103 ,
           8.398174  ,  -2.788003  ],
        [-13.952421  ,  27.236431  , -21.672535  , ...,  12.315258  ,
          32.0066    ,  -6.390406  ]]], dtype=float32)],
   'outputs': array([[[ 0.00751659,  0.09138028, -0.06991552, ..., -0.0409005 ,
          0.05420982, -0.07181367],
        [ 0.01611666,  0.06133565, -0.08272089, ..., -0.02539468,
          0.04614223,  0.00876877],
        [ 0.02076137,  0.03587089, -0.06820213, ..., -0.00

 ('encoder.encoders.4.self_attn',
  {'inputs': [array([[[-0.05228097,  0.06201516,  0.00130919, ..., -0.01374381,
         -0.02591483,  0.0260192 ],
        [-0.06036652,  0.01290737, -0.00631236, ..., -0.02088571,
         -0.01652842,  0.08022394],
        [-0.0553437 , -0.03886166,  0.00770401, ...,  0.007958  ,
          0.01077095,  0.05185469],
        ...,
        [-0.12514165,  0.05376235, -0.0053    , ..., -0.04581168,
         -0.01290986,  0.02736306],
        [-0.0979616 ,  0.06427226, -0.02083853, ...,  0.00592195,
         -0.01674246,  0.03994178],
        [-0.04960535,  0.08008427, -0.02123182, ...,  0.04382845,
          0.06238564, -0.01150056]]], dtype=float32),
              array([[[-0.05228097,  0.06201516,  0.00130919, ..., -0.01374381,
         -0.02591483,  0.0260192 ],
        [-0.06036652,  0.01290737, -0.00631236, ..., -0.02088571,
         -0.01652842,  0.08022394],
        [-0.0553437 , -0.03886166,  0.00770401, ...,  0.007958  ,
          0.01077095,  0.

   'outputs': array([[[[1.28924409e-02, 1.15619227e-02, 1.62432957e-02, ...,
          1.55036571e-03, 1.83840550e-03, 8.08214955e-03],
         [1.14138443e-02, 1.06398882e-02, 1.39948353e-02, ...,
          1.56855979e-03, 1.68076041e-03, 7.09761260e-03],
         [7.57302251e-03, 7.66204949e-03, 1.03819687e-02, ...,
          8.18590634e-04, 8.12382612e-04, 4.49197274e-03],
         ...,
         [1.06342032e-03, 1.40158401e-03, 2.37235683e-03, ...,
          8.74870494e-02, 7.38600567e-02, 1.69973165e-01],
         [8.22014292e-04, 1.22496474e-03, 1.77637232e-03, ...,
          1.40282869e-01, 9.92255658e-02, 5.05210347e-02],
         [3.30465124e-03, 6.55118609e-03, 7.44430674e-03, ...,
          5.76230660e-02, 1.38060600e-01, 3.10819656e-01]],

        [[2.65638772e-02, 2.02408284e-02, 2.99586914e-02, ...,
          2.46638674e-02, 3.56723703e-02, 3.15921232e-02],
         [2.44804714e-02, 1.59275923e-02, 2.69811153e-02, ...,
          2.28534099e-02, 3.47735807e-02, 2.57274341e

 ('encoder.encoders.9',
  {'inputs': [array([[[ -16.219551 ,   16.759592 ,  151.72212  , ...,  -34.341003 ,
         -136.93933  ,  -86.93538  ],
        [  -5.5395107,   -0.966053 ,  177.07857  , ...,  -42.25737  ,
         -130.9163   ,  -91.049324 ],
        [ -16.136148 ,  -27.81179  ,  193.8418   , ...,  -40.8717   ,
         -121.16845  ,  -99.74114  ],
        ...,
        [  92.9171   ,   33.495987 ,  103.03801  , ...,  -70.81036  ,
          -35.37113  ,  -85.91923  ],
        [ 179.462    ,   52.991184 ,   98.54468  , ..., -122.20373  ,
          -65.54701  ,  -78.735504 ],
        [ 208.51074  ,  106.99331  ,   59.525856 , ..., -134.05621  ,
          -22.398554 , -145.97534  ]]], dtype=float32),
              array([[[ True,  True,  True,  True,  True,  True,  True,  True,  True,
          True,  True,  True,  True,  True,  True,  True,  True,  True,
          True,  True,  True,  True,  True,  True,  True,  True,  True,
          True,  True,  True,  True,  True,  True,  T

In [151]:
pprint(list(backward_dict.items()))

[('ctc',
  {'grad_ins': [array([1.], dtype=float32)],
   'grad_outs': [array(1., dtype=float32)]}),
 ('ctc.ctc_loss',
  {'grad_ins': [array([[[-2.50339508e-06,  8.36855714e-17,  4.37998011e-08, ...,
          2.12219220e-09,  8.19503493e-11,  8.44874800e-17]],

       [[-2.74181366e-06,  1.02890230e-16,  4.18336121e-08, ...,
          2.67791656e-09,  8.76090103e-11,  1.03734405e-16]],

       [[-2.74181366e-06,  1.01774185e-16,  3.91751094e-08, ...,
          2.66057598e-09,  8.98137953e-11,  1.02287957e-16]],

       ...,

       [[-3.11136246e-05,  1.04247151e-16,  9.80279765e-07, ...,
          1.15061827e-09,  2.81249218e-10,  1.15424544e-16]],

       [[-3.60012054e-05,  1.65361253e-16,  1.06062316e-06, ...,
          2.14111706e-09,  3.82189114e-10,  1.84023983e-16]],

       [[-3.61204147e-05,  1.46941224e-16,  1.33046319e-06, ...,
          2.12634266e-09,  3.29507643e-10,  1.62932902e-16]]],
      dtype=float32),
                None,
                None,
                Non

  {'grad_ins': [array([[[-7.8413226e-10, -2.7915867e-10,  1.0742558e-09, ...,
         -5.2512339e-10,  4.2949683e-10,  7.9769158e-10],
        [-7.8580858e-10, -2.6359748e-10,  1.0370076e-09, ...,
         -5.3824506e-10,  4.3037282e-10,  8.3007162e-10],
        [-7.5526502e-10, -2.5204955e-10,  9.8573949e-10, ...,
         -5.1912774e-10,  4.1574036e-10,  8.0142498e-10],
        ...,
        [-5.9756342e-09,  4.3513322e-09,  9.2861518e-10, ...,
          1.2481014e-09,  2.5227651e-09,  2.7728548e-09],
        [-5.4931948e-09,  4.3238688e-09,  9.2904795e-11, ...,
         -1.8067592e-10,  1.8732387e-09,  3.2911878e-09],
        [-6.3127081e-09,  3.7884007e-09,  7.2657402e-10, ...,
         -1.9260193e-10,  5.9639621e-10,  3.4758023e-09]]], dtype=float32),
                array([-1.86262419e-04, -6.39107719e-04,  3.06588452e-04, -1.02476403e-03,
       -7.40233227e-05, -1.06717530e-03, -1.04299339e-03,  7.79446680e-04,
       -1.39905533e-04,  3.71596543e-04, -7.15430418e-04, -5.069948

  {'grad_ins': [array([[[0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        ...,
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.]]], dtype=float32)],
   'grad_outs': [array([[[-1.03178834e-04,  7.06091523e-05, -3.57133336e-04, ...,
          1.58483948e-04,  6.07702532e-06,  5.00906550e-04],
        [-9.20851526e-05,  7.19266391e-05, -3.15915211e-04, ...,
          1.33855545e-04, -7.92372339e-06,  4.47002763e-04],
        [-8.54709215e-05,  6.81058737e-05, -2.96287792e-04, ...,
          1.23860300e-04, -9.62487866e-06,  4.25703940e-04],
        ...,
        [ 1.26605701e-05,  1.21962483e-04, -1.76597270e-04, ...,
          6.79234290e-05,  9.14590273e-05,  1.37164621e-04],
        [ 1.19976212e-05,  1.12664704e-04, -1.62899203e-04, ...,
          6.36449477e-05,  8.44165406e-05,  1.29877983e-04],
        [ 8.49900607e-06,  8.26261821e-05, -1.21591314e-04

 ('encoder.encoders.9.feed_forward.w_2',
  {'grad_ins': [array([[[ 1.0890202e-05, -1.5668633e-06, -1.6059610e-06, ...,
          9.1367394e-07,  3.0797787e-06, -4.2804763e-06],
        [ 1.1744996e-05,  4.8972817e-07, -1.5083841e-06, ...,
         -5.8612125e-07,  4.2577576e-06, -4.0192876e-06],
        [ 1.1194672e-05,  4.2714868e-07, -1.7954146e-06, ...,
         -9.6267763e-07,  4.5451825e-06, -3.9881934e-06],
        ...,
        [-7.2710662e-07, -9.3432516e-07,  2.7109845e-06, ...,
          2.9392977e-06, -5.6208391e-06, -6.7707751e-06],
        [ 1.9677518e-06,  4.8159768e-06,  2.1828096e-06, ...,
          2.6041973e-06, -8.8494753e-06, -5.7065790e-06],
        [ 1.6571362e-06,  5.6935587e-06, -3.0427594e-07, ...,
         -6.2272238e-07, -7.9295996e-06, -4.9636492e-06]]], dtype=float32),
                array([ 8.66261893e-04, -2.70567660e-04, -4.27620776e-04, -3.29824467e-03,
        7.08721578e-04, -2.65993993e-03, -2.13322841e-04,  8.90064926e-04,
       -6.16403937e-04, -6

  {'grad_ins': [array([[[-3.9885734e-05,  1.9307516e-05,  2.3225813e-05, ...,
          9.2820574e-06,  6.5383094e-05, -9.1613329e-06],
        [-4.6671161e-05,  3.5961937e-05,  6.7645274e-06, ...,
          4.5611250e-06,  5.1031158e-05, -2.7930837e-06],
        [-5.8274483e-05,  4.4905315e-05,  6.6209468e-06, ...,
          3.1036639e-06,  5.0175611e-05, -5.8653250e-06],
        ...,
        [ 1.2449526e-05, -3.0980438e-05,  3.9483559e-05, ...,
         -9.6329954e-05,  6.3514899e-06,  2.4730267e-05],
        [-5.2144933e-05,  4.1854400e-05, -7.3122836e-05, ...,
         -5.9454229e-05, -2.5760099e-05, -8.0961545e-06],
        [ 3.1647625e-05, -5.6470559e-05,  2.0660924e-05, ...,
         -5.0338753e-05, -2.8560007e-06,  1.0430916e-05]]], dtype=float32),
                array([-4.97080199e-02,  7.57626165e-03, -3.09225954e-02, -3.78006734e-02,
        1.10685546e-02, -5.35881072e-02, -1.12673081e-02,  2.27051154e-02,
        4.40242104e-02,  8.33335295e-02, -3.21369059e-02,  3.098726

...

 ('encoder.encoders.3.norm1',
  {'grad_ins': [array([[[-8.7196177e-06,  1.8629498e-05,  1.5767530e-06, ...,
          1.8885341e-06,  3.5928057e-05,  1.5692021e-06],
        [ 2.7669216e-06,  7.6077185e-06,  1.8896597e-05, ...,
         -4.1636117e-06,  4.1428058e-05, -5.3117710e-06],
        [ 2.2361359e-05,  1.0167918e-05,  1.7734887e-06, ...,
          6.6991579e-06,  5.9145939e-05, -8.1932376e-06],
        ...,
        [ 1.1496254e-05, -9.4062971e-06,  2.5607812e-06, ...,
          2.6157992e-05,  4.0048931e-06,  2.6608970e-05],
        [-1.7682145e-05, -4.1786425e-06,  3.3125766e-06, ...,
         -2.3944933e-05, -1.0624563e-05,  1.2731633e-05],
        [-1.9933336e-06,  2.3966510e-05,  2.6225944e-06, ...,
          4.2293941e-06,  3.3155626e-05,  1.3537068e-05]]], dtype=float32),
                array([ 4.25032824e-02, -2.14494746e-02, -4.64770431e-03,  8.59496966e-02,
       -1.47962635e-02, -3.09461951e-02,  3.82900208e-01, -1.49033703e-02,
       -3.50581072e-02, -4.42296602e-

 ('encoder.encoders.2.self_attn.linear_k',
  {'grad_ins': [array([[[ 5.72263307e-05,  1.14046425e-05,  1.26370687e-05, ...,
         -3.64849169e-04, -7.86988123e-04,  2.09782171e-04],
        [-6.12109143e-05,  2.39655947e-05,  4.68052531e-05, ...,
         -1.76317277e-04, -4.31936176e-04,  9.25417262e-05],
        [ 2.74797549e-05, -2.68358162e-05,  4.56655471e-05, ...,
         -4.70619241e-04, -6.09423791e-04,  3.58186953e-04],
        ...,
        [ 1.32859903e-04, -4.73461077e-05,  3.51262656e-06, ...,
         -2.27963217e-04, -2.53685459e-04,  2.79755535e-04],
        [-1.81583644e-04, -1.13555652e-04,  8.85576374e-05, ...,
         -1.55008267e-04, -5.29389188e-04,  2.93750694e-04],
        [-9.91110792e-05, -2.49129312e-06,  4.95229833e-05, ...,
         -2.53028265e-04, -4.03091661e-04,  2.61495792e-04]]],
      dtype=float32),
                array([ 1.88447302e-09,  1.17347554e-09, -9.89530236e-10,  5.38420863e-10,
       -3.06272341e-09, -3.84170562e-09,  5.95173333e-09,

  {'grad_ins': [array([[[ 1.0878213e-05, -2.1674663e-05,  1.9575329e-05, ...,
          9.0855956e-06, -2.3399731e-05, -2.1155247e-05],
        [ 2.2034406e-05,  3.5795820e-05,  5.3859385e-05, ...,
          1.8762321e-05, -2.0338721e-06, -9.8223272e-06],
        [-1.1987060e-05,  8.1063263e-07, -1.1492466e-06, ...,
          8.1819717e-06,  7.2868861e-05, -1.9447285e-05],
        ...,
        [-5.5309953e-05, -4.9550214e-05,  2.9378783e-05, ...,
          1.6413731e-05, -3.3127228e-05, -8.7153239e-07],
        [-3.5904581e-05, -2.2141314e-05, -1.8435447e-05, ...,
         -1.8039113e-05, -9.2024071e-05,  2.0144831e-05],
        [ 1.3847513e-05,  2.0253901e-07,  3.7543177e-06, ...,
         -1.8958148e-05, -6.5284701e-05,  6.2770137e-05]]], dtype=float32),
                array([ 1.28603785e-03, -1.16122188e-03,  1.75608159e-03, -1.44022820e-03,
        6.69162109e-05, -1.18091865e-03,  1.80209172e-03,  9.46583576e-04,
       -6.20502862e-04,  6.18041318e-04, -1.08647328e-05,  3.261776

  {'grad_ins': [array([[[-7.5936873e-07, -4.0469236e-06,  4.8688835e-06, ...,
         -3.7237469e-06,  2.9390312e-06,  5.4163766e-06],
        [-7.1800091e-06,  3.2131097e-06, -2.8736131e-06, ...,
         -4.0490545e-06,  1.4741929e-06,  2.2029066e-05],
        [-1.1036166e-05, -1.0669604e-05, -9.6748108e-06, ...,
         -8.3757213e-06,  6.0544021e-06,  1.5941794e-05],
        ...,
        [-1.0258489e-05,  1.0795425e-05,  5.6076929e-06, ...,
         -2.7658659e-06, -1.9911527e-06,  1.0326576e-05],
        [-8.2195975e-06, -3.9631727e-06,  3.9393508e-06, ...,
         -1.1541731e-05,  5.8732797e-07,  1.6537399e-06],
        [ 2.6876153e-06, -1.9073827e-06,  1.8787914e-06, ...,
          1.2661400e-05, -2.3563205e-06,  2.3787748e-06]]], dtype=float32),
                array([-1.65740669e-01,  1.11864822e-03, -2.61588581e-03,  2.14161375e-03,
       -4.26953584e-02, -3.63521427e-02,  3.99958668e-03, -1.07978852e-02,
        7.16012269e-02, -3.07309534e-02, -7.61018172e-02,  1.007681

   'grad_outs': [array([[[-5.0316181e-04, -6.9621124e-04,  6.7324861e-04, ...,
          2.6824881e-04, -2.0255095e-04, -2.4344762e-04],
        [-3.1612918e-04,  9.4870559e-04,  1.2216796e-03, ...,
          1.5594788e-04,  1.3738776e-04,  6.2671822e-04],
        [-1.2854614e-03, -6.8001455e-04, -6.8211470e-05, ...,
          4.2724202e-04,  2.1057387e-03,  1.9316320e-04],
        ...,
        [-1.4105279e-03, -1.6683645e-03,  2.5207669e-04, ...,
          4.6348758e-04, -8.4976346e-04,  5.0271675e-04],
        [-1.2494111e-03, -1.9164791e-03, -6.7316572e-04, ...,
         -1.1609219e-03, -2.1847268e-03,  5.4835406e-04],
        [-1.1504941e-04, -1.5803514e-03, -5.0628860e-04, ...,
         -7.2876445e-04, -1.6785556e-03,  9.1195776e-04]]], dtype=float32)]}),
 ('encoder.embed.conv.3',
  {'grad_ins': [array([[[[0., 0., 0., ..., 0., 0., 0.],
         [0., 0., 0., ..., 0., 0., 0.],
         [0., 0., 0., ..., 0., 0., 0.],
         ...,
         [0., 0., 0., ..., 0., 0., 0.],
         [0.,

In [178]:
print(backward_dict['ctc.ctc_loss']['grad_outs'])
print(backward_dict['ctc.ctc_loss']['grad_ins'])
print(backward_dict['ctc.ctc_lo']['grad_ins'][0])
print(backward_dict['ctc.ctc_lo']['grad_ins'][1])

[array([1.], dtype=float32)]
[array([[[-2.50339508e-06,  8.36855714e-17,  4.37998011e-08, ...,
          2.12219220e-09,  8.19503493e-11,  8.44874800e-17]],

       [[-2.74181366e-06,  1.02890230e-16,  4.18336121e-08, ...,
          2.67791656e-09,  8.76090103e-11,  1.03734405e-16]],

       [[-2.74181366e-06,  1.01774185e-16,  3.91751094e-08, ...,
          2.66057598e-09,  8.98137953e-11,  1.02287957e-16]],

       ...,

       [[-3.11136246e-05,  1.04247151e-16,  9.80279765e-07, ...,
          1.15061827e-09,  2.81249218e-10,  1.15424544e-16]],

       [[-3.60012054e-05,  1.65361253e-16,  1.06062316e-06, ...,
          2.14111706e-09,  3.82189114e-10,  1.84023983e-16]],

       [[-3.61204147e-05,  1.46941224e-16,  1.33046319e-06, ...,
          2.12634266e-09,  3.29507643e-10,  1.62932902e-16]]],
      dtype=float32), None, None, None]
[[[-2.50339508e-06  8.36855714e-17  4.37998011e-08 ...  2.12219220e-09
    8.19503493e-11  8.44874800e-17]
  [-2.74181366e-06  1.02890230e-16  4.1833

In [183]:
grad_dict={}
for key, val in model.named_parameters():
    if 'ctc' not in key:
        continue
    if 'weight' in key:
        print(key, val.grad.t().detach().numpy())
        grad_dict[key] = val.grad.t().detach().numpy()
    else:
        print(key, val.grad.detach().numpy())
        grad_dict[key] = val.grad.detach().numpy()

ctc.ctc_lo.weight [[-4.8778719e-01  6.0130427e-13 -3.1780367e-04 ...  2.0314937e-08
  -5.0664734e-10  6.6247995e-13]
 [ 1.2689343e-01  4.6998050e-13 -6.2227007e-03 ... -1.4220235e-09
   1.2722685e-09  5.0751840e-13]
 [-1.6759640e-01  4.7447750e-13 -1.6318382e-03 ...  1.0639946e-08
  -4.2976129e-09  5.1606310e-13]
 ...
 [ 1.1945984e-01 -7.6746086e-13  1.4032462e-03 ... -4.9666298e-09
  -8.6895852e-10 -8.4059870e-13]
 [-5.1776640e-02 -2.6462575e-14  5.4250457e-03 ... -1.2460214e-09
  -6.5056005e-10 -3.3405353e-14]
 [ 2.3638242e-01 -5.2414919e-13 -5.6176288e-03 ... -2.1122869e-08
  -9.9013251e-09 -5.7118551e-13]]
ctc.ctc_lo.bias [-7.5972462e-01  2.4060894e-12  1.3913637e-02 ...  9.5985001e-08
  5.8366982e-08  2.5355482e-12]


In [184]:
!rm -rf espnet.grad
paddle.save(grad_dict, 'espnet.grad')

In [39]:

pmodel={
    'forward':forward_dict,
    'backward': backward_dict,
    'model': paddle_model_state_dict,
    'xs':x,
    'ys':y,
    'ilens': ilen,
    'olens': olen,
}

In [44]:
!rm -rf espnet.model

In [45]:
paddle.save(pmodel, 'espnet.model')

In [49]:
print(forward_dict.values())

dict_values([{'inputs': [array([[[[-0.74641937, -0.58889526, -0.79081845, ...,  1.2798967 ,
           0.22447938, -0.11255249],
         [-0.74641937, -0.574557  , -0.9586555 , ...,  1.3187659 ,
           0.24862868,  0.06486106],
         [-0.51503205, -0.41683638, -0.6949115 , ...,  1.3654089 ,
           0.28082776,  0.04357147],
         ...,
         [-0.65000796, -0.54588056, -0.9586555 , ...,  0.7260699 ,
          -0.24240735, -0.19061443],
         [-0.74641937, -0.6175717 , -0.8387718 , ...,  0.7131443 ,
          -0.2343576 ,  0.11453688],
         [-0.47646755, -0.37382168, -0.79081845, ...,  1.0933245 ,
          -0.2343576 ,  0.44807434]]]], dtype=float32)], 'outputs': array([[[[-2.3296108e+00, -2.3804862e+00, -2.2985189e+00, ...,
          -2.2790453e+00, -1.7673831e+00, -2.1839311e+00],
         [-2.4855013e+00, -2.5069976e+00, -2.5415361e+00, ...,
          -2.0678055e+00, -1.9863954e+00, -2.2065032e+00],
         [-2.1821668e+00, -2.6111586e+00, -2.4770577e+00, ...,